In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [2]:
m = 105
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)

# 현재시각
present_time = fmins[m]
sigtable_start = fmins[m] - 1200
sim_start = fmins[m] - 900
sim_end = fmins[m] - 600

# network and dataframes
net = sumolib.net.readNet('../../Data/networks/sn.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)
plan = pd.read_csv('../../data/tables/plan.csv', index_col=0)
match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
histid = pd.read_csv(f'../../Data/tables/histids/histids_{present_time}.csv', index_col=0)
histid = histid.reset_index(drop=True).drop(columns=['inter_no'])

# helper dictionaries
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':['u60'], 'i7':[], 'i8':[], 'i9':[]}
node_ids = sorted(inter_node.node_id.unique())
parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]

In [3]:
node_ids

['c30',
 'i0',
 'i1',
 'i2',
 'i3',
 'i6',
 'i7',
 'i8',
 'i9',
 'u00',
 'u20',
 'u30',
 'u31',
 'u32',
 'u60']

In [4]:
node2mincycle = {}
for inter_no in sorted(plan.inter_no.unique()):
    mincycle = plan[plan.inter_no==inter_no].cycle.min()
    parent_id = inter2node[inter_no]
    node2mincycle[parent_id] = mincycle
    for child_id in pa2ch:
        node2mincycle[child_id] = mincycle
for node_id in sorted(node2mincycle):
    print(node_id, node2mincycle[node_id])

c30 140
i0 150
i1 150
i2 150
i3 150
i6 150
i7 150
i8 150
i9 150
u00 160
u20 150
u60 150


In [5]:
def make_histids(histid, match6, parent_ids, pa2ch):
    new_histids = []
    for parent_id in parent_ids:
        for child_id in pa2ch[parent_id]:
            new_histid = histid.copy()[histid.node_id==parent_id]
            new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
            for i, row in new_histid.iterrows():
                phas_A = row.phas_A
                phas_B = row.phas_B
                new_match = match6[match6.node_id==child_id]
                Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]
                if ~ Arow[['inc_edge', 'out_edge']].isna().all().all():
                    inc_edge = Arow.iloc[0].inc_edge
                    out_edge = Arow.iloc[0].out_edge
                    new_histid.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge, out_edge]
                Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
                if ~ Brow[['inc_edge', 'out_edge']].isna().all().all():
                    inc_edge = Brow.iloc[0].inc_edge
                    out_edge = Brow.iloc[0].out_edge
                    new_histid.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge, out_edge]
                new_histid.loc[i, 'node_id'] = child_id
            new_histids.append(new_histid)
    new_histids = pd.concat(new_histids)
    histids = pd.concat([histid.copy(), new_histids])
    histids = histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
    return histids

In [6]:
def initialize_states(net, nodes, histids):
    node2init = {}
    for node in nodes:
        node_id = node.getID()
        conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
        conns = [c for c in conns if c[0] >= 0]
        conns = sorted(conns, key=lambda x: x[0])
        state = []
        for i, ci in conns:
            if ci.getTLLinkIndex() < 0:
                continue
            are_foes = False
            for j, cj in conns:
                if ci.getTo() == cj.getTo():
                    continue
                if node.areFoes(i, j):
                    are_foes = True
                    break
            state.append('r' if are_foes else 'g')
        node2init[node_id] = state

    # 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
    for _, row in histids.iterrows():
        node_id = row['node_id']
        inc_edge_A = row.inc_edge_A
        inc_edge_B = row.inc_edge_B
        out_edge_A = row.out_edge_A
        out_edge_B = row.out_edge_B

        if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
            pass
        else:
            inc_edge_A = net.getEdge(inc_edge_A)
            out_edge_A = net.getEdge(out_edge_A)
            for conn in inc_edge_A.getConnections(out_edge_A):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    node2init[node_id][index] = 'r'

        if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
            pass
        else:
            inc_edge_B = net.getEdge(inc_edge_B)
            out_edge_B = net.getEdge(out_edge_B)
            for conn in inc_edge_B.getConnections(out_edge_B):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    node2init[node_id][index] = 'r'
    return node2init

In [7]:
def make_sigtable(histids, node2init, net):
    sigtable = histids.copy()
    sigtable['init_state'] = sigtable['node_id'].map(node2init)
    sigtable['state'] = sigtable['init_state'].map(lambda x:''.join(x))
    for i, row in sigtable.iterrows():
        node_id = row.node_id
        inc_edge_A = row.inc_edge_A
        inc_edge_B = row.inc_edge_B
        out_edge_A = row.out_edge_A
        out_edge_B = row.out_edge_B
        state = copy.deepcopy(node2init)[node_id]
        if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
            pass
        else:
            inc_edge_A = net.getEdge(inc_edge_A)
            out_edge_A = net.getEdge(out_edge_A)
            for conn in inc_edge_A.getConnections(out_edge_A):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    state[index] = 'G'
            sigtable.at[i, 'state'] = ''.join(state)

        if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
            pass
        else:
            inc_edge_B = net.getEdge(inc_edge_B)
            out_edge_B = net.getEdge(out_edge_B)
            for conn in inc_edge_B.getConnections(out_edge_B):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    state[index] = 'G'
            sigtable.at[i, 'state'] = ''.join(state)
    sigtable = sigtable.dropna(subset='state')
    sigtable = sigtable.reset_index(drop=True)
    sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
    # sigtable = sigtable[sigtable.start_unix >= sigtable_start]
    sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
    sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
    sigtable['start_dt'] = sigtable['start_unix'].apply(lambda x:datetime.fromtimestamp(x))
    return sigtable

In [8]:
def make_Sigtable(sigtable):
    Sigtable = []
    for node_id, group in sigtable.groupby('node_id'):
        new_rows_list = []
        for i in range(1, len(group)):
            prev_row = group.iloc[i-1:i].copy()
            next_row = group.iloc[i:i+1].copy()
            new_rows = pd.concat([prev_row, prev_row, next_row]).reset_index(drop=True)
            new_rows.loc[0, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_g'
            new_rows.loc[0, 'duration'] = new_rows.loc[0, 'duration'] - 5
            new_rows.loc[1, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_y'
            new_rows.loc[1, 'duration'] = 4
            yellow_state = ''
            red_state = ''
            for a, b in zip(prev_row.state.iloc[0], next_row.state.iloc[0]):
                if a == 'G' and b == 'r':
                    yellow_state += 'y'
                    red_state += 'r'
                else:
                    yellow_state += a
                    red_state += a
            new_rows.loc[2, 'phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '__r'
            new_rows.loc[2, 'duration'] = 1
            new_rows.loc[1, 'state'] = yellow_state
            new_rows.loc[2, 'state'] = red_state
            new_rows_list.append(new_rows)
        next_row['phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '_g'
        next_row['duration'] -= 5
        # next_row.loc['duration'] -= 5
        new_rows_list.append(next_row)
        new_rows = pd.concat(new_rows_list)
        Sigtable.append(new_rows)
    Sigtable = pd.concat(Sigtable).sort_values(by=['node_id', 'start_unix', 'phase_sumo']).reset_index(drop=True)
    return Sigtable

In [9]:
# # sigtable 시작시각  : 현재시각 - 1200 = 08:25
# # 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# # 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# # 현재시각           : 08:45
# print(datetime.fromtimestamp(sigtable_start))
# print(datetime.fromtimestamp(sim_start))
# print(datetime.fromtimestamp(sim_end))
# print(datetime.fromtimestamp(present_time))

In [10]:
def make_SIGTABLE(Sigtable, sim_start, sim_end):
    offsets = {}
    SIGTABLE = []
    for node_id, group in Sigtable.groupby('node_id'):
        lsbs = group[group['start_unix'] < sim_start]['start_unix'].max() # the last start_unix before sim_start
        offsets[node_id] = lsbs - sim_start
        group = group[(group['start_unix'] < sim_end) & (group['start_unix'] >= lsbs)]
        SIGTABLE.append(group)
    SIGTABLE = pd.concat(SIGTABLE)
    return SIGTABLE, offsets

def make_signals(SIGTABLE, offsets, present_time):
    strings = ['<additional>\n']
    for node_id, group in SIGTABLE.groupby('node_id'):
        strings.append(f'    <tlLogic id="{node_id}" type="static" programID="{node_id}_prog" offset="{offsets[node_id]}">\n')
        for i, row in group.iterrows():
            duration = row.duration
            state = row.state
            strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
        strings.append('    </tlLogic>\n')
    strings.append('</additional>')
    strings = ''.join(strings)
    # 저장
    path_output = f'../../Data/networks/sn_{present_time}.add.xml'
    with open(path_output, 'w') as f:
        f.write(strings)

In [11]:
def generate_signals(m):
    midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
    next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
    fmins = range(midnight, next_day, 300)

    # 현재시각
    present_time = fmins[m]
    sigtable_start = fmins[m] - 1200
    sim_start = fmins[m] - 900
    sim_end = fmins[m] - 600
    
    # network and dataframes
    net = sumolib.net.readNet('../../Data/networks/sn.net.xml')
    inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)
    match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
    match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
    histid = pd.read_csv(f'../../Data/tables/histids/histids_{present_time}.csv', index_col=0)
    histid = histid.reset_index(drop=True).drop(columns=['inter_no'])
    
    # helper dictionaries
    inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
    node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
    pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':['u60'], 'i7':[], 'i8':[], 'i9':[]}
    node_ids = sorted(inter_node.node_id.unique())
    parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
    nodes = [net.getNode(node_id) for node_id in node_ids]

    # histids
    histids = make_histids(histid, match6, parent_ids, pa2ch)

    # node2init
    node2init = initialize_states(net, nodes, histids)

    # sigtable
    sigtable = make_sigtable(histids, node2init, net)

    # Sigtable
    Sigtable = make_Sigtable(sigtable)

    # SIGTABLE
    SIGTABLE, offsets = make_SIGTABLE(Sigtable, sim_start, sim_end)

    make_signals(SIGTABLE, offsets, present_time)
    print(f'A signal file (add.xml) has been created for the timeslot between {datetime.fromtimestamp(sim_start)} and {datetime.fromtimestamp(sim_end)}')

In [12]:
generate_signals(105)

A signal file (add.xml) has been created for the timeslot between 2024-01-05 08:30:00 and 2024-01-05 08:35:00
